In [8]:
# IMPORT STATEMENTS
import cv2
import re
import numpy as np
from matplotlib import pyplot as plt
from mpl_toolkits.axes_grid1 import make_axes_locatable, axes_size
import matplotlib.patches as patches
import matplotlib.colors as colors
import PIL
import math
get_ipython().magic('matplotlib inline')
import pandas as pd
import seaborn as sns
import json
from scipy.stats import fisher_exact, ttest_ind
from collections import Counter
from pprint import pprint
import os
import pickle
import sys
sys.path.append("/Users/rohan/public_html/Hegemon/")
sys.path.append("BoNE")
import StepMiner as smn
import HegemonUtil as hu

# Imports all the methods written by Dr. Sahoo for BE paper (iNetMed-120920.ipynb)
# Perform same functions as perl scripts (some functionality is limited)
from BINetwork import *

acolor = ["#00CC00", "#D8A03D","#EC008C",
          'cyan', "#B741DC", "#808285",
          'blue', 'black', 'green', 'red',
          'orange', 'brown', 'pink', 'purple']

try:
    reload  # Python 2.7
except NameError:
    try:
        from importlib import reload  # Python 3.4+
    except ImportError:
        from imp import reload  # Python 3.0 - 3.3     

import matplotlib
matplotlib.rcParams['pdf.fonttype'] = 42
matplotlib.rcParams['ps.fonttype'] = 42

def getPDF(cfile):
    from matplotlib.backends.backend_pdf import PdfPages
    pdf = PdfPages(cfile)
    return pdf

def closePDF(pdf):
    import datetime
    d = pdf.infodict()
    d['Title'] = 'Plots'
    d['Author'] = 'Debashis Sahoo'
    d['Subject'] = "AD"
    d['Keywords'] = 'disease training validation ROC'
    d['CreationDate'] = datetime.datetime(2021, 6, 19)
    d['ModDate'] = datetime.datetime.today()
    pdf.close()

In [3]:
db = hu.Database("/Users/rohan/public_html/Hegemon/explore.conf")
dbid = "G19"
h = hu.Hegemon(db.getDataset(dbid))
h.init()
h.initPlatform()
h.initSurv()
atype = h.getSurvName("c cell type")
hu.uniq(atype)

[4,
 'c cell type',
 'Hematopoietic stem cell_CD133+ CD34dim',
 'Colony Forming Unit-Granulocyte',
 'Mature NK cell_CD56- CD16+ CD3-',
 'CD4+ Central Memory',
 'CD4+ Effector Memory',
 'Naive CD4+ T-cell',
 'Megakaryocyte/ erythroid progenitor',
 'Erythroid_CD34- CD71+ GlyA-',
 'CD8+ Central Memory',
 'Naive CD8+ T-cell',
 'Eosinophill',
 'Basophils',
 'CD8+ Effector Memory RA',
 'CD8+ Effector Memory',
 'Colony Forming Unit-Megakaryocytic',
 'Granulocyte (Neutrophilic Metamyelocyte)',
 'Erythroid_CD34- CD71- GlyA+',
 'Mature B-cell class able to switch',
 'Naïve B-cells',
 'Erythroid_CD34- CD71lo GlyA+',
 'Hematopoietic stem cell_CD38- CD34+',
 'Mature NK cell_CD56- CD16- CD3-',
 'Early B-cell',
 'Granulocyte (Neutrophil)',
 'Myeloid Dendritic Cell',
 'Erythroid_CD34+ CD71+ GlyA-',
 'Plasmacytoid Dendritic Cell',
 'Pro B-cell',
 'NKT',
 'Common myeloid progenitor',
 'Mature B-cell class switched',
 'Granulocyte/monocyte progenitor',
 'Megakaryocyte',
 'Erythroid_CD34- CD71+ GlyA+',
 '

In [9]:
# Write a class for Hematopoiesis Analysis (HPAnalysis) to get data and generate plots easily.
import bone
reload(bone)
cf = "/Users/rohan/public_html/Hegemon/explore.conf"

class HPAnalysis(bone.IBDAnalysis):

    def __init__(self):
        bone.IBDAnalysis.__init__(self)

    def getNorvershtern2011(self):
        self.prepareData("G19")
        atype = self.h.getSurvName('c cell type')
        atypes = atype
        ahash = {atype[i]:i for i in range(len(atype))}
        self.initData(atype, atypes, ahash)   
        
    # Examples with documentation:
    
    def getSuntsova2019(self, tn=1):
        self.prepareData("GL33")
        atype = self.h.getSurvName('c tissue')
        atypes = ['Colon'] # of all tissues, we want only colon.
        ahash = {'Colon':0, 'Colon, epithelium':0} # Combine colon and colon, epithelium
        if (tn == 2): # selecting some specific patient samples.
            atype = self.h.headers
            atypes = ['C', 'B', 'S']
            ahash = {'GSM3415805':0, 'GSM3415851':0, 'GSM3415854':1,
                     'GSM3415888':1, 'GSM3415810':2,'GSM3415864':2}
        self.initData(atype, atypes, ahash)
        
    def getPetersDf(self, tn=1):
        self.prepareDataDf("PLP7")
        atype = hu.getHegemonPatientData(self.dbid, 'c clinical condition')[1]
        ahash = {'Ulcerative Colitis':1, 'control':0, "Crohn's disease":2}
        atypes = ['Normal', 'UC', 'CD']
        # in this if statement, see if we want to analyze UC and CD separately or combined.
        # this assigns 1 to UC and CD which are types of IBD, hence combining them into a single type IBD.
        if (tn == 2):
            atypes = ['Normal', 'IBD']
            ahash = {"control": 0, "Ulcerative Colitis":1, "Crohn's disease":1} 
        self.initData(atype, atypes, ahash)
        
    def plotViolinBar(ana, desc=None):
        fig = plt.figure(figsize=(4,4), dpi=100)
        plt.subplots_adjust(hspace=0.5, wspace=0.5)
        ax1 = plt.subplot2grid((4, 1), (0, 0))
        ax2 = plt.subplot2grid((4, 1), (1, 0), rowspan=3)
        params = {'spaceAnn': len(ana.order)/len(ana.atypes), 'tAnn': 1, 'widthAnn':1,
                  'genes': [], 'ax': ax1, 'acolor': acolor}
        ax = ana.printTitleBar(params)
        res = ana.getROCAUC()
        ax.text(len(ana.cval[0]), 4, res)
        if desc is not None:
            ax.text(-1, 2, desc, horizontalalignment='right',
                        verticalalignment='center')
        params = {'spaceAnn': len(ana.order)/len(ana.atypes), 'tAnn': 1, 'widthAnn':1,
                'genes': [], 'ax': ax2, 'acolor': acolor, 'vert': 0}
        ax = ana.printViolin(None, params)
        return fig

    def plotDensityBar(ana, desc=None):
        fig = plt.figure(figsize=(4,4), dpi=100)
        plt.subplots_adjust(hspace=0.5, wspace=0.5)
        ax1 = plt.subplot2grid((4, 1), (0, 0))
        ax2 = plt.subplot2grid((4, 1), (1, 0), rowspan=3)
        params = {'spaceAnn': len(ana.order)/len(ana.atypes), 'tAnn': 1, 'widthAnn':1,
                  'genes': [], 'ax': ax1, 'acolor': acolor}
        ax = ana.printTitleBar(params)
        res = ana.getMetrics(ana.cval[0])
        ax.text(len(ana.cval[0]), 4, ",".join(res))
        if desc is not None:
            ax.text(-1, 2, desc, horizontalalignment='right',
                        verticalalignment='center')
        ax = ana.densityPlot(ax2, acolor)
        return fig

    def processData(ana, l1, wt1, desc=None, violin=1):
        ana.orderData(l1, wt1)
        if (violin == 1):
            return plotViolinBar(ana, desc)
        return plotDensityBar(ana, desc)


In [10]:
# DEBUG THIS: getVInfo isn't working because vinfo files are not stored in /booleanfs/sahoo/Networks/Survival/
# for some reason. All other files are there though. Also, vinfo file in data dir was empty, so I regenerated it.
ana = HPAnalysis()
ana.getNorvershtern2011()
df = pd.read_csv(ana.h.rdataset.getVInfo(), sep="\t")

Novershtern 2011 Human Hematopoiesis (n = 211)
GSE24759 http://hegemon.ucsd.edu/Tools/explore.php?key=polyps&id=G19
211 [1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 5, 0, 0, 0, 0, 0, 0, 7, 0, 4, 0, 0, 0, 0, 0, 0, 7, 0, 0, 0, 0, 0, 4, 0, 0, 0, 0, 0, 0, 0, 5, 0, 5, 6, 0, 5, 0, 7, 0, 4, 0, 0, 5, 7, 0, 4, 5, 4, 0, 4, 0, 0, 0, 0, 4, 0, 5, 0, 0, 0, 0, 9, 0, 7, 6, 6, 7, 7, 0, 5, 5, 0, 4, 4, 6, 4, 10, 5, 5, 7, 5, 5, 7] GSE24759 http://hegemon.ucsd.edu/Tools/explore.php?key=polyps&id=G19 G19


FileNotFoundError: [Errno 2] No such file or directory: '/booleanfs/sahoo/Networks/Survival/novershtern-2011-hh-vinfo.txt'